In [ ]:
from google.colab import files
uploaded = files.upload()

Saving deliverytime.txt to deliverytime (1).txt


In [ ]:
!pip install pandas numpy scikit-learn

In [ ]:
import pandas as pd
import numpy as np
import plotly.express as px
data = pd.read_csv("deliverytime.txt")
print(data.head())

     ID Delivery_person_ID  Delivery_person_Age  Delivery_person_Ratings  \
0  4607     INDORES13DEL02                   37                      4.9   
1  B379     BANGRES18DEL02                   34                      4.5   
2  5D6D     BANGRES19DEL01                   23                      4.4   
3  7A6A    COIMBRES13DEL02                   38                      4.7   
4  70A2     CHENRES12DEL01                   32                      4.6   

   Restaurant_latitude  Restaurant_longitude  Delivery_location_latitude  \
0            22.745049             75.892471                   22.765049   
1            12.913041             77.683237                   13.043041   
2            12.914264             77.678400                   12.924264   
3            11.003669             76.976494                   11.053669   
4            12.972793             80.249982                   13.012793   

   Delivery_location_longitude Type_of_order Type_of_vehicle  Time_taken(min)  
0     

In [ ]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 45593 entries, 0 to 45592
Data columns (total 11 columns):
 #   Column                       Non-Null Count  Dtype  
---  ------                       --------------  -----  
 0   ID                           45593 non-null  object 
 1   Delivery_person_ID           45593 non-null  object 
 2   Delivery_person_Age          45593 non-null  int64  
 3   Delivery_person_Ratings      45593 non-null  float64
 4   Restaurant_latitude          45593 non-null  float64
 5   Restaurant_longitude         45593 non-null  float64
 6   Delivery_location_latitude   45593 non-null  float64
 7   Delivery_location_longitude  45593 non-null  float64
 8   Type_of_order                45593 non-null  object 
 9   Type_of_vehicle              45593 non-null  object 
 10  Time_taken(min)              45593 non-null  int64  
dtypes: float64(5), int64(2), object(4)
memory usage: 3.8+ MB


In [ ]:
data.shape

(45593, 11)

In [ ]:
data.isnull().sum()

ID                             0
Delivery_person_ID             0
Delivery_person_Age            0
Delivery_person_Ratings        0
Restaurant_latitude            0
Restaurant_longitude           0
Delivery_location_latitude     0
Delivery_location_longitude    0
Type_of_order                  0
Type_of_vehicle                0
Time_taken(min)                0
dtype: int64

In [ ]:
R_E = 6371 #km
def deg_to_rad(degrees):
    return degrees * (np.pi/180)

# calculating the distance between two points using the haversine formula

def calculate_distance_haversine(lati1, longi1, lati2, longi2):
    diff_lat = deg_to_rad(lati2-lati1)
    diff_lon = deg_to_rad(longi2-longi1)
    a = np.sin(diff_lat/2)*2 + np.cos(deg_to_rad(lati1)) * np.cos(deg_to_rad(lati2)) * np.sin(diff_lon/2)*2
    c = 2 * np.arctan2(np.sqrt(a), np.sqrt(1-a))
    return R_E * c

# Calculating the distance between each pair of points
data['distance'] = np.nan

for i in range(len(data)):
    data.loc[i, 'distance'] = calculate_distance_haversine(data.loc[i, 'Restaurant_latitude'],
                                        data.loc[i, 'Restaurant_longitude'],
                                        data.loc[i, 'Delivery_location_latitude'],
                                        data.loc[i, 'Delivery_location_longitude'])

<ipython-input-35-0c6c5bb69465>:11: RuntimeWarning:

invalid value encountered in sqrt



In [ ]:
print(data.head(10))

     ID Delivery_person_ID  Delivery_person_Age  Delivery_person_Ratings  \
0  4607     INDORES13DEL02                   37                      4.9   
1  B379     BANGRES18DEL02                   34                      4.5   
2  5D6D     BANGRES19DEL01                   23                      4.4   
3  7A6A    COIMBRES13DEL02                   38                      4.7   
4  70A2     CHENRES12DEL01                   32                      4.6   
5  9BB4      HYDRES09DEL03                   22                      4.8   
6  95B4   RANCHIRES15DEL01                   33                      4.7   
7  9EB2      MYSRES15DEL02                   35                      4.6   
8  1102      HYDRES05DEL02                   22                      4.8   
9  CDCD      DEHRES17DEL01                   36                      4.2   

   Restaurant_latitude  Restaurant_longitude  Delivery_location_latitude  \
0            22.745049             75.892471                   22.765049   
1          

In [ ]:
figure = px.scatter(data_frame = data,
                    x="distance",
                    y="Time_taken(min)",
                    size="Time_taken(min)",
                    trendline="ols",
                    title = "Relationship Between Distance and Time Taken")
figure.show()

In [ ]:
figure = px.scatter(data_frame = data,
                    x="Delivery_person_Age",
                    y="Time_taken(min)",
                    size="Time_taken(min)",
                    color = "distance",
                    trendline="ols",
                    title = "Relationship Between Time Taken and Age")
figure.show()

In [ ]:
figure = px.scatter(data_frame = data,
                    x="Delivery_person_Ratings",
                    y="Time_taken(min)",
                    size="Time_taken(min)",
                    color = "distance",
                    trendline="ols",
                    title = "Relationship Between The Time Taken and Delivery Persons Ratings")
figure.show()

In [ ]:
from sklearn.impute import SimpleImputer
from sklearn.model_selection import train_test_split

# Define features and target variable
X = data[['distance', 'Delivery_person_Age', 'Delivery_person_Ratings']]  # Features
y = data['Time_taken(min)']  # Target variable

# Handle missing values using mean imputation
imputer = SimpleImputer(strategy='mean')
X_imputed = imputer.fit_transform(X)

# Split the data into training and test sets
X_train, X_test, y_train, y_test = train_test_split(X_imputed, y, test_size=0.2, random_state=42)


In [ ]:
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
from sklearn.ensemble import RandomForestRegressor

# Train Random Forest Regressor
rf_model = RandomForestRegressor(random_state=42)
rf_model.fit(X_train, y_train)
rf_predictions = rf_model.predict(X_test)

# Evaluate Random Forest Regressor
rf_mse = mean_squared_error(y_test, rf_predictions)
rf_mae = mean_absolute_error(y_test, rf_predictions)
rf_r2 = r2_score(y_test, rf_predictions)

print(f"Random Forest - MSE: {rf_mse:.2f}, MAE: {rf_mae:.2f}, R^2 Score: {rf_r2:.2f}")


Random Forest - MSE: 66.55, MAE: 6.33, R^2 Score: 0.24


In [ ]:
from sklearn.neighbors import KNeighborsRegressor

# Train K-Nearest Neighbors Regressor
knn_model = KNeighborsRegressor(n_neighbors=5)
knn_model.fit(X_train, y_train)
knn_predictions = knn_model.predict(X_test)

# Evaluate K-Nearest Neighbors Regressor
knn_mse = mean_squared_error(y_test, knn_predictions)
knn_mae = mean_absolute_error(y_test, knn_predictions)
knn_r2 = r2_score(y_test, knn_predictions)

print(f"K-Nearest Neighbors - MSE: {knn_mse:.2f}, MAE: {knn_mae:.2f}, R^2 Score: {knn_r2:.2f}")


K-Nearest Neighbors - MSE: 72.78, MAE: 6.69, R^2 Score: 0.17


In [ ]:
from sklearn.tree import DecisionTreeRegressor

# Train Decision Tree Regressor
dt_model = DecisionTreeRegressor(random_state=42)
dt_model.fit(X_train, y_train)
dt_predictions = dt_model.predict(X_test)

# Evaluate Decision Tree Regressor
dt_mse = mean_squared_error(y_test, dt_predictions)
dt_mae = mean_absolute_error(y_test, dt_predictions)
dt_r2 = r2_score(y_test, dt_predictions)

print(f"Decision Tree - MSE: {dt_mse:.2f}, MAE: {dt_mae:.2f}, R^2 Score: {dt_r2:.2f}")


Decision Tree - MSE: 105.58, MAE: 7.92, R^2 Score: -0.20


In [ ]:
from sklearn.linear_model import LinearRegression

# Train Linear Regression
lr_model = LinearRegression()
lr_model.fit(X_train, y_train)
lr_predictions = lr_model.predict(X_test)

# Evaluate Linear Regression
lr_mse = mean_squared_error(y_test, lr_predictions)
lr_mae = mean_absolute_error(y_test, lr_predictions)
lr_r2 = r2_score(y_test, lr_predictions)

print(f"Linear Regression - MSE: {lr_mse:.2f}, MAE: {lr_mae:.2f}, R^2 Score: {lr_r2:.2f}")


Linear Regression - MSE: 71.77, MAE: 6.63, R^2 Score: 0.18


In [ ]:
# Function to take input from the user
def take_user_input():
    try:
        distance = float(input("Enter the distance (in km): "))
        age = int(input("Enter the delivery person's age: "))
        ratings = float(input("Enter the delivery person's ratings (0-5): "))
        return np.array([[distance, age, ratings]])
    except ValueError:
        print("Invalid input! Please enter numerical values.")
        return take_user_input()
# Get user input
user_input = take_user_input()
# Use the imputer to handle any missing values in user input
user_input_imputed = imputer.transform(user_input)
# Predict using all models
rf_pred = rf_model.predict(user_input_imputed)
knn_pred = knn_model.predict(user_input_imputed)
dt_pred = dt_model.predict(user_input_imputed)
lr_pred = lr_model.predict(user_input_imputed)
# Print the predictions
print(f"Predicted Time Taken by Random Forest: {rf_pred[0]:.2f} minutes")
print(f"Predicted Time Taken by K-Nearest Neighbors: {knn_pred[0]:.2f} minutes")
print(f"Predicted Time Taken by Decision Tree: {dt_pred[0]:.2f} minutes")
print(f"Predicted Time Taken by Linear Regression: {lr_pred[0]:.2f} minutes")


Enter the distance (in km): 2
Enter the delivery person's age: 19
Enter the delivery person's ratings (0-5): 4
Predicted Time Taken by Random Forest: 26.28 minutes
Predicted Time Taken by K-Nearest Neighbors: 15.80 minutes
Predicted Time Taken by Decision Tree: 29.00 minutes
Predicted Time Taken by Linear Regression: 26.91 minutes


/usr/local/lib/python3.10/dist-packages/sklearn/base.py:465: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names



In [ ]:
# Cross-Validation and Model Evaluation
from sklearn.model_selection import cross_val_score
# Function to evaluate the model using cross-validation
def evaluate_model(model, X, y, model_name):
    # Perform 5-fold cross-validation for mean squared error
    mse_scores = cross_val_score(model, X, y, scoring='neg_mean_squared_error', cv=5)
    mae_scores = cross_val_score(model, X, y, scoring='neg_mean_absolute_error', cv=5)
    r2_scores = cross_val_score(model, X, y, scoring='r2', cv=5)
    # Convert negative MSE and MAE to positive
    mse_scores = -mse_scores
    mae_scores = -mae_scores
    # Calculate mean and standard deviation for each metric
    print(f"{model_name} - Mean MSE: {mse_scores.mean():.2f} (Std: {mse_scores.std():.2f})")
    print(f"{model_name} - Mean MAE: {mae_scores.mean():.2f} (Std: {mae_scores.std():.2f})")
    print(f"{model_name} - Mean R² Score: {r2_scores.mean():.2f} (Std: {r2_scores.std():.2f})")
    print("-" * 60)
# Evaluate Random Forest
evaluate_model(rf_model, X_imputed, y, "Random Forest")
# Evaluate K-Nearest Neighbors
evaluate_model(knn_model, X_imputed, y, "K-Nearest Neighbors")
# Evaluate Decision Tree
evaluate_model(dt_model, X_imputed, y, "Decision Tree")
# Evaluate Linear Regression
evaluate_model(lr_model, X_imputed, y, "Linear Regression")


Random Forest - Mean MSE: 67.45 (Std: 1.48)
Random Forest - Mean MAE: 6.38 (Std: 0.06)
Random Forest - Mean R² Score: 0.23 (Std: 0.02)
------------------------------------------------------------
K-Nearest Neighbors - Mean MSE: 72.83 (Std: 0.97)
K-Nearest Neighbors - Mean MAE: 6.72 (Std: 0.04)
K-Nearest Neighbors - Mean R² Score: 0.17 (Std: 0.01)
------------------------------------------------------------
Decision Tree - Mean MSE: 108.33 (Std: 1.88)
Decision Tree - Mean MAE: 8.00 (Std: 0.07)
Decision Tree - Mean R² Score: -0.23 (Std: 0.02)
------------------------------------------------------------
Linear Regression - Mean MSE: 71.71 (Std: 1.19)
Linear Regression - Mean MAE: 6.65 (Std: 0.05)
Linear Regression - Mean R² Score: 0.19 (Std: 0.01)
------------------------------------------------------------
